## Import des librairies

In [47]:
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
import csv
from surprise import SVD
from surprise.prediction_algorithms.co_clustering import CoClustering
from surprise.prediction_algorithms.knns import KNNBasic 
from surprise.prediction_algorithms.matrix_factorization import NMF, SVDpp
from surprise.prediction_algorithms.slope_one import SlopeOne
from surprise.dataset import Dataset
from surprise import Reader
from surprise import accuracy
from surprise.model_selection import train_test_split, cross_validate, GridSearchCV
import re
from sklearn.preprocessing import LabelEncoder, StandardScaler 
import folium
from sklearn.cluster import KMeans, DBSCAN
from sklearn.linear_model import LogisticRegression

## Création du dataframe

Récupération des colonnes à étudier à partir de la base de données des arbres de Paris

In [2]:
localisation = []
genre = []
stade_dev = []
arr = []
adresse = []

with open('les-arbres.csv') as csvDataFile:
    csvReader = csv.reader(csvDataFile, delimiter=';')
    for row in csvReader:
        localisation.append(row[16])
        genre.append(row[9])
        stade_dev.append(row[14])
        arr.append(row[3])
        adresse.append(row[6])

In [3]:
df_stade_dev = pd.DataFrame(stade_dev)
df_genre = pd.DataFrame(genre)
df_localisation = pd.DataFrame(localisation)
df_arr = pd.DataFrame(arr)
df_adresse = pd.DataFrame(adresse)

Récupération de la colonne Lieu/Adresse

In [4]:
df_adresse.rename(columns={0:"LIEU/ADRESSE"}, inplace=True)
df_adresse

LIEU/ADRESSE
0                                          LIEU / ADRESSE
1       CIMETIERE D''IVRY / AVENUE TRANSVERSALE N1 / D...
2                                      PLACE HENRI ROLLET
3                                        AVENUE DAUMESNIL
4                                       AVENUE DE MESSINE
...                                                   ...
204722                                        RUE GIFFARD
204723                               ROUTE DE LA PYRAMIDE
204724   ECOLE MATERNELLE / 5 AVENUE DE LA PORTE BRANCION
204725                           PARC DES BUTTES CHAUMONT
204726                                 PARC ANDRE CITROEN

[204727 rows x 1 columns]

Récupération de la colonne ARRONDISSEMENT

In [5]:
df_arr.rename(columns={0:"ARRONDISSEMENT"}, inplace=True)
df_arr

ARRONDISSEMENT
0          ARRONDISSEMENT
1            VAL-DE-MARNE
2         PARIS 15E ARRDT
3         PARIS 12E ARRDT
4          PARIS 8E ARRDT
...                   ...
204722    PARIS 13E ARRDT
204723  BOIS DE VINCENNES
204724    PARIS 15E ARRDT
204725    PARIS 19E ARRDT
204726    PARIS 15E ARRDT

[204727 rows x 1 columns]

Récupération de la colonne GENRE

In [6]:
df_genre.rename(columns={0:"GENRE"}, inplace=True)
df_genre

GENRE
0          GENRE
1       Platanus
2       Aesculus
3       Platanus
4       Platanus
...          ...
204722    Cornus
204723     Tilia
204724    Prunus
204725      Acer
204726     Fagus

[204727 rows x 1 columns]

Récupération de la géolocalisation des arbres

In [7]:
df_localisation.rename(columns={0:"geo_point_2d"}, inplace=True)
df_localisation

geo_point_2d
0                      geo_point_2d
1       48.8143225054,2.36626830927
2       48.8359698888,2.29322150925
3       48.8384903343,2.39832788916
4       48.8755110103,2.31534526812
...                             ...
204722  48.8378015477,2.37296652217
204723  48.8277304429,2.45368273739
204724  48.8275223917,2.30251079924
204725  48.8773571618,2.37871097818
204726  48.8421072774,2.27349597411

[204727 rows x 1 columns]

Récupération de la colonne STADE de DEVELOPPEMENT des arbres

In [8]:
df_stade_dev.rename(columns={0:"STADE"}, inplace=True)
df_stade_dev

STADE
0       STADE DE DEVELOPPEMENT
1                           JA
2                            A
3                            J
4                            A
...                        ...
204722                        
204723                      JA
204724                       J
204725                        
204726                        

[204727 rows x 1 columns]

Préparation du Dataset de travail

In [9]:
df = df_arr.join(df_genre)
df2 = df.join(df_adresse)
df3 = df2.join(df_localisation)
df4 = df3.join(df_stade_dev)

In [10]:
df4 = df4.drop(0)

In [11]:
df4['GENRE'] = df4['GENRE'].map(lambda x: x.lower())
df4['ARRONDISSEMENT'] = df4['ARRONDISSEMENT'].map(lambda x: x.lower())
df4['LIEU/ADRESSE'] = df4['LIEU/ADRESSE'].map(lambda x: x.lower())
df4['STADE'] = df4['STADE'].map(lambda x: x.lower())

In [12]:
df4.loc[df4["GENRE"]=="betula","Allergisant"] = "1"
df4.loc[df4["GENRE"]=="cupressus","Allergisant"] = "1"
df4.loc[df4["GENRE"]=="corylus","Allergisant"] = "1"
df4.loc[df4["GENRE"]=="platanus","Allergisant"] = "1"
df4.loc[df4["GENRE"]=="olea","Allergisant"] = "1"
df4.loc[df4["GENRE"]=="fraxinus","Allergisant"] = "1"
df4.loc[df4["GENRE"]=="quercus","Allergisant"] = "1"
df4.loc[df4["GENRE"]=="carpinus betulus","Allergisant"] = "1"
df4.loc[df4["Allergisant"]!="1","Allergisant"] = "0"

In [13]:
df4

ARRONDISSEMENT     GENRE  \
1            val-de-marne  platanus   
2         paris 15e arrdt  aesculus   
3         paris 12e arrdt  platanus   
4          paris 8e arrdt  platanus   
5         paris 20e arrdt  platanus   
...                   ...       ...   
204722    paris 13e arrdt    cornus   
204723  bois de vincennes     tilia   
204724    paris 15e arrdt    prunus   
204725    paris 19e arrdt      acer   
204726    paris 15e arrdt     fagus   

                                             LIEU/ADRESSE  \
1       cimetiere d''ivry / avenue transversale n1 / d...   
2                                      place henri rollet   
3                                        avenue daumesnil   
4                                       avenue de messine   
5                                   boulevard de charonne   
...                                                   ...   
204722                                        rue giffard   
204723                               route de la pyramide   
204724   ecole maternelle / 5 avenue de la porte brancion   
204725                           parc des buttes chaumont   
204726                                 parc andre citroen   

                       geo_point_2d STADE Allergisant  
1       48.8143225054,2.36626830927    ja           1  
2       48.8359698888,2.29322150925     a           0  
3       48.8384903343,2.39832788916     j           1  
4       48.8755110103,2.31534526812     a           1  
5       48.8576865521,2.39247765288    ja           1  
...                             ...   ...         ...  
204722  48.8378015477,2.37296652217                 0  
204723  48.8277304429,2.45368273739    ja           0  
204724  48.8275223917,2.30251079924     j           0  
204725  48.8773571618,2.37871097818                 0  
204726  48.8421072774,2.27349597411                 0  

[204726 rows x 6 columns]

In [14]:
df4.loc[df4['GENRE'].str.contains("betula"),'GENRE']='1'
df4.loc[df4['GENRE'].str.contains("cupressus"),'GENRE']='2'
df4.loc[df4['GENRE'].str.contains("corylus"),'GENRE']='3'
df4.loc[df4['GENRE'].str.contains("platanus"),'GENRE']='4'
df4.loc[df4['GENRE'].str.contains("olea"),'GENRE']='5'
df4.loc[df4['GENRE'].str.contains("fraxinus"),'GENRE']='6'
df4.loc[df4['GENRE'].str.contains("quercus"),'GENRE']='7'
df4.loc[df4['GENRE'].str.contains("carpinus betulus"),'GENRE']='8'

La colonne ALLERGIE obéit à la règle suivante : seulement si l'arbre est allergisant et si son stade de développement est différent de "jeune adulte" alors une allergie peut être déclenchée.

In [15]:
df4.loc[(df4["Allergisant"]=="1") & (df4["STADE"]!="ja"), "ALLERGIE"] = "oui"
df4.loc[(df4["Allergisant"]=="0") | (df4["STADE"]=="ja"), "ALLERGIE"] = "non"

In [16]:
df4

ARRONDISSEMENT     GENRE  \
1            val-de-marne         4   
2         paris 15e arrdt  aesculus   
3         paris 12e arrdt         4   
4          paris 8e arrdt         4   
5         paris 20e arrdt         4   
...                   ...       ...   
204722    paris 13e arrdt    cornus   
204723  bois de vincennes     tilia   
204724    paris 15e arrdt    prunus   
204725    paris 19e arrdt      acer   
204726    paris 15e arrdt     fagus   

                                             LIEU/ADRESSE  \
1       cimetiere d''ivry / avenue transversale n1 / d...   
2                                      place henri rollet   
3                                        avenue daumesnil   
4                                       avenue de messine   
5                                   boulevard de charonne   
...                                                   ...   
204722                                        rue giffard   
204723                               route de la pyramide   
204724   ecole maternelle / 5 avenue de la porte brancion   
204725                           parc des buttes chaumont   
204726                                 parc andre citroen   

                       geo_point_2d STADE Allergisant ALLERGIE  
1       48.8143225054,2.36626830927    ja           1      non  
2       48.8359698888,2.29322150925     a           0      non  
3       48.8384903343,2.39832788916     j           1      oui  
4       48.8755110103,2.31534526812     a           1      oui  
5       48.8576865521,2.39247765288    ja           1      non  
...                             ...   ...         ...      ...  
204722  48.8378015477,2.37296652217                 0      non  
204723  48.8277304429,2.45368273739    ja           0      non  
204724  48.8275223917,2.30251079924     j           0      non  
204725  48.8773571618,2.37871097818                 0      non  
204726  48.8421072774,2.27349597411                 0      non  

[204726 rows x 7 columns]

In [17]:
encoder=LabelEncoder()
df4['ALLERGIE']=encoder.fit_transform(df4['ALLERGIE'])

In [18]:
df5 = pd.DataFrame(df4.geo_point_2d.str.split(",",1).tolist(), columns = ['LATITUDE','LONGITUDE'])

In [19]:
df5

LATITUDE      LONGITUDE
0       48.8143225054  2.36626830927
1       48.8359698888  2.29322150925
2       48.8384903343  2.39832788916
3       48.8755110103  2.31534526812
4       48.8576865521  2.39247765288
...               ...            ...
204721  48.8378015477  2.37296652217
204722  48.8277304429  2.45368273739
204723  48.8275223917  2.30251079924
204724  48.8773571618  2.37871097818
204725  48.8421072774  2.27349597411

[204726 rows x 2 columns]

In [20]:
df5= df5.astype(float)

In [21]:
del df4['geo_point_2d']

In [22]:
df_f = df4.join(df5)

In [23]:
df_i = df_f.loc[df_f["ARRONDISSEMENT"].str.contains('paris') == True]

In [24]:
df_i = df_i.drop(204726)

In [25]:
df_i['ARRONDISSEMENT']=encoder.fit_transform(df_i['ARRONDISSEMENT'])  

In [26]:
df_i['LIEU/ADRESSE']=encoder.fit_transform(df_i['LIEU/ADRESSE'])  

In [27]:
df_i['STADE']=encoder.fit_transform(df_i['STADE'])  

Données d'étude

In [28]:
df_i

ARRONDISSEMENT     GENRE  LIEU/ADRESSE  STADE Allergisant  ALLERGIE  \
2                    5  aesculus          2613      1           0         0   
3                    2         4            79      2           1         1   
4                   18         4           137      1           1         1   
5                   11         4           349      3           1         0   
8                    7         4           417      3           1         0   
...                ...       ...           ...    ...         ...       ...   
204719               3         7          1934      0           1         1   
204721               1         4          2205      3           1         0   
204722               3    cornus          3559      0           0         0   
204724               5    prunus          1637      2           0         0   
204725               9      acer          2313      0           0         0   

         LATITUDE  LONGITUDE  
2       48.838490   2.398328  
3       48.875511   2.315345  
4       48.857687   2.392478  
5       48.839600   2.440891  
8       48.830790   2.318618  
...           ...        ...  
204719  48.808982   2.315095  
204721  48.837802   2.372967  
204722  48.827730   2.453683  
204724  48.877357   2.378711  
204725  48.842107   2.273496  

[164150 rows x 8 columns]

In [29]:
df_a = df_i.loc[df_i["ALLERGIE"] == 1]

In [30]:
df_a.round(6)

ARRONDISSEMENT GENRE  LIEU/ADRESSE  STADE Allergisant  ALLERGIE  \
3                    2     4            79      2           1         1   
4                   18     4           137      1           1         1   
10                   4     4           338      2           1         1   
31                   5     4           406      1           1         1   
33                   3     4           409      1           1         1   
...                ...   ...           ...    ...         ...       ...   
204700              18     4          2435      2           1         1   
204701               8     4           124      1           1         1   
204707              11     4          3332      2           1         1   
204713              17     4           179      1           1         1   
204719               3     7          1934      0           1         1   

         LATITUDE  LONGITUDE  
3       48.875511   2.315345  
4       48.857687   2.392478  
10      48.839049   2.252322  
31      48.851564   2.300121  
33      48.835841   2.372595  
...           ...        ...  
204700  48.900738   2.352211  
204701  48.868624   2.301010  
204707  48.833598   2.333723  
204713  48.899201   2.336531  
204719  48.808982   2.315095  

[38557 rows x 8 columns]

In [31]:
df_a.dtypes

ARRONDISSEMENT      int32
GENRE              object
LIEU/ADRESSE        int32
STADE               int32
Allergisant        object
ALLERGIE            int32
LATITUDE          float64
LONGITUDE         float64
dtype: object

In [32]:
 manquantes = df_a.isnull().sum()
 print(manquantes)

ARRONDISSEMENT    0
GENRE             0
LIEU/ADRESSE      0
STADE             0
Allergisant       0
ALLERGIE          0
LATITUDE          0
LONGITUDE         0
dtype: int64


Il n'y a pas de données manquantes.

In [33]:
df_a.describe(include = 'all')

ARRONDISSEMENT  GENRE  LIEU/ADRESSE         STADE Allergisant  \
count     38557.000000  38557  38557.000000  38557.000000       38557   
unique             NaN      7           NaN           NaN           1   
top                NaN      4           NaN           NaN           1   
freq               NaN  29694           NaN           NaN       38557   
mean          7.921545    NaN   1606.523277      1.272895         NaN   
std           5.284194    NaN   1486.379344      0.972874         NaN   
min           0.000000    NaN      3.000000      0.000000         NaN   
25%           4.000000    NaN    333.000000      1.000000         NaN   
50%           7.000000    NaN    481.000000      1.000000         NaN   
75%          11.000000    NaN   2849.000000      2.000000         NaN   
max          19.000000    NaN   4653.000000      4.000000         NaN   

        ALLERGIE      LATITUDE     LONGITUDE  
count    38557.0  38557.000000  38557.000000  
unique       NaN           NaN           NaN  
top          NaN           NaN           NaN  
freq         NaN           NaN           NaN  
mean         1.0     48.855141      2.347439  
std          0.0      0.027045      0.050280  
min          1.0     48.742290      2.210241  
25%          1.0     48.836137      2.307724  
50%          1.0     48.854452      2.350248  
75%          1.0     48.875082      2.384337  
max          1.0     48.911473      2.469736

In [34]:
# coords = (48.856614, 2.3522219)
# map = folium.Map(location=coords, tiles='OpenStreetMap')

In [35]:
# for i,j in zip(df_i["LATITUDE"],df_i["LONGITUDE"]):
#     folium.CircleMarker(
#         location = (i, j),
#         color = 'blue',
#         fill = True,
#         fill_color = 'blue'
#     ).add_to(map)

In [36]:
# for i,j in zip(df_a["LATITUDE"],df_a["LONGITUDE"]):
#     folium.CircleMarker(
#         location = (i, j),
#         color = 'red',
#         fill = True,
#         fill_color = 'red'
#     ).add_to(map)

In [37]:
# for i in range(0,len(df_i)):
#     folium.Marker([df_i.iloc[i]['LONGITUDE'], df_i.iloc[i]['LATITUDE']]).add_to(map)

## Création du dataset

In [38]:
reader = Reader(rating_scale=(1, 164151))

Création du Dataset utilisé pour la prédiction. Choix de la prédiction de la latitude de genre d'arbres allergisant et non allergisant.

In [39]:
df_etude_2 = Dataset.load_from_df(df_a[['LATITUDE', 'LONGITUDE','GENRE']], reader)
#y1 = df_a['ALLERGIE']

## Test et validation de différents algorithmes de prédiction

In [40]:
algo1 = SVD()
cross_validate(algo1, df_etude_2, measures=['RMSE', 'MAE'], cv=5, verbose=True)

Evaluating RMSE, MAE of algorithm SVD on 5 split(s).

                  Fold 1  Fold 2  Fold 3  Fold 4  Fold 5  Mean    Std     
RMSE (testset)    1.1318  1.1439  1.1203  1.1306  1.1356  1.1325  0.0077  
MAE (testset)     0.6363  0.6412  0.6264  0.6347  0.6357  0.6348  0.0048  
Fit time          3.88    3.82    4.00    3.92    3.96    3.92    0.06    
Test time         0.15    0.13    0.16    0.13    0.10    0.13    0.02    


{'test_rmse': array([1.13183227, 1.1439425 , 1.12032458, 1.13064261, 1.13563562]),
 'test_mae': array([0.63631236, 0.64119957, 0.62635334, 0.63471497, 0.63566773]),
 'fit_time': (3.880823850631714,
  3.8174033164978027,
  4.004842281341553,
  3.92043137550354,
  3.959005355834961),
 'test_time': (0.14927458763122559,
  0.13459086418151855,
  0.15846920013427734,
  0.13322806358337402,
  0.09662938117980957)}

In [41]:
algo_NMF =  NMF()
cross_validate(algo_NMF, df_etude_2, measures=['RMSE', 'MAE'], cv=5, verbose=True)

Evaluating RMSE, MAE of algorithm NMF on 5 split(s).

                  Fold 1  Fold 2  Fold 3  Fold 4  Fold 5  Mean    Std     
RMSE (testset)    1.1358  1.1404  1.1253  1.1461  1.1147  1.1325  0.0112  
MAE (testset)     0.6364  0.6435  0.6292  0.6418  0.6234  0.6349  0.0076  
Fit time          12.00   11.86   13.39   13.63   13.68   12.91   0.81    
Test time         0.32    0.09    0.16    0.15    0.16    0.18    0.07    


{'test_rmse': array([1.13578158, 1.14043133, 1.12528386, 1.14612047, 1.11470698]),
 'test_mae': array([0.63642072, 0.64348172, 0.62923768, 0.64181706, 0.62335683]),
 'fit_time': (11.998594284057617,
  11.85928726196289,
  13.39474892616272,
  13.627981424331665,
  13.676787614822388),
 'test_time': (0.31701231002807617,
  0.09448027610778809,
  0.16190528869628906,
  0.1506803035736084,
  0.15970683097839355)}

In [42]:
algo2 = CoClustering()
cross_validate(algo2, df_etude_2, measures=['RMSE', 'MAE'], cv=5, verbose=True)

Evaluating RMSE, MAE of algorithm CoClustering on 5 split(s).

                  Fold 1  Fold 2  Fold 3  Fold 4  Fold 5  Mean    Std     
RMSE (testset)    1.1279  1.1407  1.1311  1.1353  1.1275  1.1325  0.0050  
MAE (testset)     0.6312  0.6402  0.6366  0.6375  0.6286  0.6348  0.0043  
Fit time          12.22   12.37   12.17   13.62   12.63   12.60   0.54    
Test time         0.13    0.14    0.14    0.18    0.31    0.18    0.07    


{'test_rmse': array([1.12789341, 1.1406603 , 1.13108278, 1.13529864, 1.12747905]),
 'test_mae': array([0.6312232 , 0.64022197, 0.63663391, 0.63751768, 0.62864127]),
 'fit_time': (12.219463348388672,
  12.36835789680481,
  12.1719069480896,
  13.624338865280151,
  12.631787538528442),
 'test_time': (0.13063573837280273,
  0.14261698722839355,
  0.14272451400756836,
  0.17731714248657227,
  0.30859947204589844)}

In [43]:
# algo3 = SlopeOne()
# cross_validate(algo3, df_etude_2, measures=['RMSE', 'MAE'], cv=5, verbose=True)

In [44]:
# algo4 = KNNBasic ()
# cross_validate(algo4, df_etude_2, measures=['RMSE', 'MAE'], cv=5, verbose=True)

In [60]:
X = StandardScaler().fit_transform(df_a)

algo5 = DBSCAN(eps=0.3, min_samples=7).fit(X)
labels = algo5.labels_
n_clusters_ = len(set(labels)) - (1 if -1 in labels else 0)
n_noise_ = list(labels).count(-1)

In [61]:
print('Estimated number of clusters: %d' % n_clusters_)
print('Estimated number of noise points: %d' % n_noise_)

Estimated number of clusters: 305
Estimated number of noise points: 12782


In [ ]:
# param_grid = {'n_epochs': [5, 10], 'lr_all': [0.022, 0.023, 0.024]}
# gs = GridSearchCV(algo2, param_grid, measures=['rmse', 'mae'], cv=3)

# gs.fit(df_etude)

# # best RMSE score
# print(gs.best_score['rmse'])

# # combination of parameters that gave the best RMSE score
# print(gs.best_params['rmse'])

## Utilisation de l'algorithme de prédiction. 
L'algorithme choisi est le CoClustering.

In [62]:
train_2, test_2 = train_test_split(df_etude_2, test_size=.25)
algo = CoClustering()
algo.fit(train_2)
predictions_1 = algo.test(test_2)
accuracy.rmse(predictions_1)

accuracy.mae(predictions_1)

predictions_1 = algo.fit(train_2).test(test_2)
predictions_1

RMSE: 1.1384
MAE:  0.6399


[Prediction(uid=48.8389053607, iid=2.28406148061, r_ui=4.0, est=4.156758999896255, details={'was_impossible': False}),
 Prediction(uid=48.9008451372, iid=2.41112587717, r_ui=4.0, est=4.156758999896255, details={'was_impossible': False}),
 Prediction(uid=48.8207771539, iid=2.45392066383, r_ui=6.0, est=4.156758999896255, details={'was_impossible': False}),
 Prediction(uid=48.8224033936, iid=2.34654958263, r_ui=4.0, est=4.156758999896255, details={'was_impossible': False}),
 Prediction(uid=48.8879639866, iid=2.36210229412, r_ui=4.0, est=4.156758999896255, details={'was_impossible': False}),
 Prediction(uid=48.8542077536, iid=2.3041257692, r_ui=4.0, est=4.156758999896255, details={'was_impossible': False}),
 Prediction(uid=48.8918024234, iid=2.38663437386, r_ui=4.0, est=4.156758999896255, details={'was_impossible': False}),
 Prediction(uid=48.8411163054, iid=2.33711271709, r_ui=4.0, est=4.156758999896255, details={'was_impossible': False}),
 Prediction(uid=48.857824688, iid=2.30408129143, 

In [63]:
train_2, test_2 = train_test_split(df_etude_2, test_size=.25)
algo = SVD()
algo.fit(train_2)
predictions_2 = algo.test(test_2)
accuracy.rmse(predictions_2)

accuracy.mae(predictions_2)

predictions_2 = algo.fit(train_2).test(test_2)
predictions_2

RMSE: 1.1253
MAE:  0.6335


[Prediction(uid=48.8717201647, iid=2.2619661232, r_ui=4.0, est=4.161358370508697, details={'was_impossible': False}),
 Prediction(uid=48.8395010936, iid=2.39448218077, r_ui=4.0, est=4.161358370508697, details={'was_impossible': False}),
 Prediction(uid=48.889571984, iid=2.36713706871, r_ui=6.0, est=4.161358370508697, details={'was_impossible': False}),
 Prediction(uid=48.8356870098, iid=2.33182962551, r_ui=4.0, est=4.161358370508697, details={'was_impossible': False}),
 Prediction(uid=48.9032105424, iid=2.41290246149, r_ui=4.0, est=4.161358370508697, details={'was_impossible': False}),
 Prediction(uid=48.9046854821, iid=2.41480351104, r_ui=6.0, est=4.161358370508697, details={'was_impossible': False}),
 Prediction(uid=48.8299061728, iid=2.46083021163, r_ui=4.0, est=4.161358370508697, details={'was_impossible': False}),
 Prediction(uid=48.8477719819, iid=2.38993734324, r_ui=4.0, est=4.161358370508697, details={'was_impossible': False}),
 Prediction(uid=48.892882635, iid=2.34139455031, r

In [64]:
train_2, test_2 = train_test_split(df_etude_2, test_size=.25)
algo = NMF()
algo.fit(train_2)
predictions_3 = algo.test(test_2)
accuracy.rmse(predictions_3)

accuracy.mae(predictions_3)

predictions_3 = algo.fit(train_2).test(test_2)
predictions_3

RMSE: 1.1450
MAE:  0.6415


[Prediction(uid=48.8507581629, iid=2.31142730252, r_ui=4.0, est=4.158764740464087, details={'was_impossible': True, 'reason': 'User and item are unknown.'}),
 Prediction(uid=48.8570881474, iid=2.36048515572, r_ui=7.0, est=4.158764740464087, details={'was_impossible': True, 'reason': 'User and item are unknown.'}),
 Prediction(uid=48.8939985849, iid=2.33410895362, r_ui=4.0, est=4.158764740464087, details={'was_impossible': True, 'reason': 'User and item are unknown.'}),
 Prediction(uid=48.8792160627, iid=2.37899033103, r_ui=4.0, est=4.158764740464087, details={'was_impossible': True, 'reason': 'User and item are unknown.'}),
 Prediction(uid=48.8317653884, iid=2.35911176273, r_ui=3.0, est=4.158764740464087, details={'was_impossible': True, 'reason': 'User and item are unknown.'}),
 Prediction(uid=48.8436537759, iid=2.31217819808, r_ui=1.0, est=4.158764740464087, details={'was_impossible': True, 'reason': 'User and item are unknown.'}),
 Prediction(uid=48.8569519669, iid=2.29880856731, r_

In [65]:
lat = []
lng = []

for i in predictions_2:
    lat.append(i[0])
    lng.append(i[1])

In [66]:
df_lat = pd.DataFrame(lat)
df_lng = pd.DataFrame(lng)

In [67]:
df_lat.rename(columns={0:"LATITUDE"}, inplace=True)
df_lat

LATITUDE
0     48.871720
1     48.839501
2     48.889572
3     48.835687
4     48.903211
...         ...
9635  48.871080
9636  48.906443
9637  48.838529
9638  48.837001
9639  48.821783

[9640 rows x 1 columns]

In [68]:
df_lng.rename(columns={0:"LONGITUDE"}, inplace=True)
df_lng

LONGITUDE
0      2.261966
1      2.394482
2      2.367137
3      2.331830
4      2.412902
...         ...
9635   2.303034
9636   2.419807
9637   2.395972
9638   2.272764
9639   2.455546

[9640 rows x 1 columns]

In [69]:
df = df_lat.join(df_lng)

## Création de la map avec les zones à éviter pour cause d'allergies aux arbres allergisants

In [70]:
coords = (48.864716,2.349014)
map = folium.Map(location=coords, tiles='OpenStreetMap', zoom_start=15)

In [71]:
kmeans = KMeans(n_clusters=n_clusters_, random_state=0).fit(df)

In [72]:
for la, ln in zip(lat, lng):
    folium.CircleMarker(
        location=[la, ln],
    ).add_to(map)

In [73]:
for l in kmeans.cluster_centers_:
    folium.CircleMarker(
        location=l,
        color='red'
    ).add_to(map)

In [74]:
map

Source des données:
- Concernant l'allergie :
    - R.N.S.A (Réseau National de Surveillance Aéorobiologique agréé par le Ministère de la Santé)
    - guide d'information (www.vegetation_en_ville.org  p67-68 (sur les arbres)